# Capse.jl chains
In this notebook we will show how to use the Capse.jl emulator in combination with Turing.jl, performing a PlanckLite analysis. In particolar, we are gonna show:

- How to compute the Maximum A Posteriori (MAP), using the L-BFGS method provided by Optim.jl
- How to use Pathfinder.jl to obtain a quick posterior estimate and initialize chains
- How to use NUTS and MicroCanonical Hamiltonian MonteCarlo as sampling algorithms

Let us start initializing the Julia environment. This will download and install the precise version of the required packages.

In [1]:
using Pkg
Pkg.activate(".")
Pkg.instantiate()
Pkg.resolve()

  Activating project at `~/Desktop/papers/capse_paper/standard_emulator`
Precompiling project...
  ✓ Plots → UnitfulExt
  ✓ StatsPlots
  2 dependencies successfully precompiled in 70 seconds. 383 already precompiled.
  No Changes to `~/Desktop/papers/capse_paper/standard_emulator/Project.toml`
  No Changes to `~/Desktop/papers/capse_paper/standard_emulator/Manifest.toml`


In [2]:
using Statistics
using SimpleChains
using NPZ
using Turing
using Optim
using Pathfinder
using StatsPlots
using Capse
using BenchmarkTools
using LinearAlgebra
using NPZ
using Transducers
using PlanckLite
import MCMCChains: compute_duration
using MicroCanonicalHMC
using MCMCDiagnosticTools
using DataFrames
include("utils.jl")

[ Info: Precompiling StatsPlots [f3b207a7-027a-5e70-b257-86293d7955fd]
[ Info: Precompiling FileIOExt [f5f51d8f-5827-5d2e-939b-192fcd6ec70c]
[ Info: Precompiling IJuliaExt [2f4121a4-3b3a-5ce6-9c5e-1f2673ce168a]


extract_single (generic function with 1 method)

Here we initialize the neural network we use for the emulator.
Do not modify this cell!

In [3]:
mlpd = SimpleChain(
  static(6),
  TurboDense(tanh, 64),
  TurboDense(tanh, 64),
  TurboDense(tanh, 64),
  TurboDense(tanh, 64),
  TurboDense(tanh, 64),
  TurboDense(identity, 4999)
);

After creating the neural network, we initialize our emulators.

In [4]:
weights_folder = "../data/weights/weights_cosmopowerspace_10000/"
ℓ = npzread(weights_folder*"l.npy")

weights_TT = npzread(weights_folder*"weights_TT_lcdm.npy")
trained_emu_TT = Capse.SimpleChainsEmulator(Architecture= mlpd, Weights = weights_TT)
CℓTT_emu = Capse.CℓEmulator(TrainedEmulator = trained_emu_TT, ℓgrid = ℓ,
                             InMinMax = npzread(weights_folder*"inMinMax_lcdm.npy"),
                             OutMinMax = npzread(weights_folder*"outMinMaxCℓTT_lcdm.npy"));

In [5]:
weights_EE = npzread(weights_folder*"weights_EE_lcdm.npy")
trained_emu_EE = Capse.SimpleChainsEmulator(Architecture= mlpd, Weights = weights_EE)
CℓEE_emu = Capse.CℓEmulator(TrainedEmulator = trained_emu_EE, ℓgrid = ℓ,
                             InMinMax = npzread(weights_folder*"inMinMax_lcdm.npy"),
                             OutMinMax = npzread(weights_folder*"outMinMaxCℓEE_lcdm.npy"));

In [6]:
weights_TE = npzread(weights_folder*"weights_TE_lcdm.npy")
trained_emu_TE = Capse.SimpleChainsEmulator(Architecture= mlpd, Weights = weights_TE)
CℓTE_emu = Capse.CℓEmulator(TrainedEmulator = trained_emu_TE, ℓgrid = ℓ,
                             InMinMax = npzread(weights_folder*"inMinMax_lcdm.npy"),
                             OutMinMax = npzread(weights_folder*"outMinMaxCℓTE_lcdm.npy"));

In [7]:
weights_PP = npzread(weights_folder*"weights_PP_lcdm.npy")
trained_emu_PP = Capse.SimpleChainsEmulator(Architecture= mlpd, Weights = weights_PP)
CℓPP_emu = Capse.CℓEmulator(TrainedEmulator = trained_emu_PP, ℓgrid = ℓ,
                             InMinMax = npzread(weights_folder*"inMinMax_lcdm.npy"),
                             OutMinMax = npzread(weights_folder*"outMinMaxCℓPP_lcdm.npy"));

## PlanckLite & Turing

Here we are going tyo create some functions to analyze Planck data.
The first function, given a list of arguments, retrieves the binned $C_\ell$'s 

In [8]:
lsTT = 2:2508
lsTE = 2:1996
facTT=lsTT.*(lsTT.+1)./(2*π)
facTE=lsTE.*(lsTE.+1)./(2*π)

function call_emu_planck(θ, Emu_TT, Emu_TE, Emu_EE, facTT, facTE)
    return PlanckLite.bin_Cℓ(Capse.get_Cℓ(θ, Emu_TT)[1:2507]./facTT,
                            Capse.get_Cℓ(θ, Emu_TE)[1:1995]./facTE,
                            Capse.get_Cℓ(θ, Emu_EE)[1:1995]./facTE)
end

call_emu_planck (generic function with 1 method)

This other function is a closure, defining a more manageable version of the same function (in this way we don't have to pass some fixed arguments)

In [9]:
theory_planck(θ) = call_emu_planck(θ, CℓTT_emu, CℓTE_emu, CℓEE_emu, facTT, facTE)

theory_planck (generic function with 1 method)

In [10]:
x = rand(6)
@benchmark theory_planck($x)

BenchmarkTools.Trial: 10000 samples with 1 evaluation.
 Range (min … max):  271.677 μs …   4.697 ms  ┊ GC (min … max): 0.00% … 86.59%
 Time  (median):     311.678 μs               ┊ GC (median):    0.00%
 Time  (mean ± σ):   341.573 μs ± 294.787 μs  ┊ GC (mean ± σ):  6.63% ±  7.07%

           ▂█▇▅▂                                                 
  ▂▂▂▂▂▂▃▄▆█████▇▆▅▅▅▅▄▃▃▃▃▃▃▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▁▁▂▂▂▁▂ ▃
  272 μs           Histogram: frequency by time          470 μs <

 Memory estimate: 664.31 KiB, allocs estimate: 8877.

Since the Covariance matrix we are gonna use does not depend on the model parameters, we can define the following quantities

$\Gamma = \mathrm{sqrt}(\Lambda)$

$i\Gamma=\mathrm{inv}(\Gamma)$

$D = i\Gamma \cdot d$

We can now sample a MvNormal with an easier covariance matrix

$D \sim \mathrm{MvNormal}(i\Gamma\cdot t(\theta), I)$

The advantage of this reparametrization is that we compute the inverse of a matrix just once and not at every step of the MCMC, without resoirting to any approximation: the two likelihood defined are mathematically equivalent.

In [11]:
Γ = sqrt(PlanckLite.cov)
iΓ = inv(Γ)
D = iΓ * PlanckLite.data;

Although this is a bit different from the way we are used to code likelihoods in cosmology, it is easy to explain how to use a Probabilistic Programming Language (PPL) such as Turing.

When we use the "$\sim$" symbol, we are saying that the left-hand-side is sampled from the distribution on the right-hand-side

In [12]:
@model function CMB_planck(D, iΓ)
    #prior on model parameters
    ln10As ~ Uniform(0.25, 0.35)
    ns     ~ Uniform(0.88, 1.06)
    h0     ~ Uniform(0.60, 0.80)
    ωb     ~ Uniform(0.1985, 0.25)
    ωc     ~ Uniform(0.08, 0.20)
    τ      ~ Normal(0.0506, 0.0086)
    yₚ     ~ Normal(1.0, 0.0025)

    θ = [10*ln10As, ns, 100*h0, ωb/10, ωc, τ]
    #compute theoretical prediction
    pred = iΓ * theory_planck(θ) ./(yₚ^2)
    #compute likelihood
    D ~ MvNormal(pred, I)

    return nothing
end

CMB_model_planck = CMB_planck(D, iΓ);

Let us perform the MAP computation. Turing has been interfaced with Optim, which provides some powerful minimization methods such as L-BFGS.

In [13]:
bestfit_Planck = optimize(CMB_model_planck, MAP(), Optim.Options(iterations=100000, allow_f_increases=true))
@benchmark optimize(CMB_model_planck, MAP(), Optim.Options(iterations=100000, allow_f_increases=true))

BenchmarkTools.Trial: 16 samples with 1 evaluation.
 Range (min … max):  216.358 ms … 593.796 ms  ┊ GC (min … max): 8.60% … 7.65%
 Time  (median):     292.249 ms               ┊ GC (median):    7.87%
 Time  (mean ± σ):   320.350 ms ± 100.472 ms  ┊ GC (mean ± σ):  7.67% ± 0.47%

  ▁ ▁▁ █▁▁   ▁ █   ▁      ▁    ▁▁      ▁                      ▁  
  █▁██▁███▁▁▁█▁█▁▁▁█▁▁▁▁▁▁█▁▁▁▁██▁▁▁▁▁▁█▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁█ ▁
  216 ms           Histogram: frequency by time          594 ms <

 Memory estimate: 350.72 MiB, allocs estimate: 897703.

The minimization takes less than half a second!

We are going to run 6 parallel chains, with 500 adaptation steps and 5'000 steps (note that Turing will not retrieve the burn-in steps)

In [14]:
nsteps = 5000
nadapts = 500
nchains = 6

6

Before starting chains, let us use Pathfinder. This will deliver an approximation to the posterior

In [15]:
result_multi = multipathfinder(CMB_model_planck, 10000; nruns=8, executor=Transducers.PreferParallel())

┌ Warning: 2 (0.6%) updates to the inverse Hessian estimate were rejected to keep it positive definite.
└ @ Pathfinder ~/.julia/packages/Pathfinder/1B4yO/src/singlepath.jl:212
┌ Warning: 1 (0.3%) updates to the inverse Hessian estimate were rejected to keep it positive definite.
└ @ Pathfinder ~/.julia/packages/Pathfinder/1B4yO/src/singlepath.jl:212
┌ Warning: 2 (0.5%) updates to the inverse Hessian estimate were rejected to keep it positive definite.
└ @ Pathfinder ~/.julia/packages/Pathfinder/1B4yO/src/singlepath.jl:212
┌ Warning: 2 (0.6%) updates to the inverse Hessian estimate were rejected to keep it positive definite.
└ @ Pathfinder ~/.julia/packages/Pathfinder/1B4yO/src/singlepath.jl:212
┌ Warning: 1 (0.3%) updates to the inverse Hessian estimate were rejected to keep it positive definite.
└ @ Pathfinder ~/.julia/packages/Pathfinder/1B4yO/src/singlepath.jl:212
┌ Warning: Pareto shape k = 0.7 > 0.7. Resulting importance sampling estimates are likely to be unstable.
└ @ PSIS ~/.ju

Multi-path Pathfinder result
  runs: 8
  draws: 10000
  Pareto shape diagnostic: 0.7 (bad)

In [16]:
@time multipathfinder(CMB_model_planck, 10000; nruns=8, executor=Transducers.PreferParallel())

┌ Warning: 1 (0.4%) updates to the inverse Hessian estimate were rejected to keep it positive definite.
└ @ Pathfinder ~/.julia/packages/Pathfinder/1B4yO/src/singlepath.jl:212
┌ Warning: 1 (0.4%) updates to the inverse Hessian estimate were rejected to keep it positive definite.
└ @ Pathfinder ~/.julia/packages/Pathfinder/1B4yO/src/singlepath.jl:212
┌ Warning: 2 (0.5%) updates to the inverse Hessian estimate were rejected to keep it positive definite.
└ @ Pathfinder ~/.julia/packages/Pathfinder/1B4yO/src/singlepath.jl:212
┌ Warning: 1 (0.2%) updates to the inverse Hessian estimate were rejected to keep it positive definite.
└ @ Pathfinder ~/.julia/packages/Pathfinder/1B4yO/src/singlepath.jl:212
┌ Warning: 1 (0.3%) updates to the inverse Hessian estimate were rejected to keep it positive definite.
└ @ Pathfinder ~/.julia/packages/Pathfinder/1B4yO/src/singlepath.jl:212
┌ Warning: 1 (0.3%) updates to the inverse Hessian estimate were rejected to keep it positive definite.
└ @ Pathfinder ~

 15.997916 seconds (306.53 M allocations: 41.000 GiB, 18.70% gc time)


Multi-path Pathfinder result
  runs: 8
  draws: 10000
  Pareto shape diagnostic: 0.7 (ok)

In [17]:
result_multi.draws_transformed

Chains MCMC chain (10000×7×1 Array{Float64, 3}):

Iterations        = 1:1:10000
Number of chains  = 1
Samples per chain = 10000
parameters        = ln10As, ns, h0, ωb, ωc, τ, yₚ

Summary Statistics
  parameters      mean       std   naive_se      mcse          ess      rhat 
      Symbol   Float64   Float64    Float64   Float64      Float64   Float64 

      ln10As    0.3051    0.0017     0.0000    0.0000    9548.7558    0.9999
          ns    0.9629    0.0045     0.0000    0.0000    9758.2291    0.9999
          h0    0.6704    0.0058     0.0001    0.0001   10164.7376    1.0002
          ωb    0.2235    0.0014     0.0000    0.0000    9801.4420    1.0001
          ωc    0.1208    0.0013     0.0000    0.0000   10171.4169    1.0002
           τ    0.0566    0.0081     0.0001    0.0001    9619.4657    0.9999
          yₚ    1.0005    0.0023     0.0000    0.0000    9689.8795    1.0001

Quantiles
  parameters      2.5%     25.0%     50.0%     75.0%     97.5% 
      Symbol   Float64   Float6

In [18]:
chain_planck_PF = combine_chains(result_multi.draws_transformed)
npzwrite("chains_Planck_PF.npy", chain_planck_PF)

Pathfinder is incredibly fast: it performed the analysis in as few as 15 seconds. However, it is an approximate method. Although it might not always used to give a faithful approximation of the posteriori, it is very useful in starting the chains as close as possible to the typical set.

Here we are gonna use some Pathfinder draws to initialize our chains.

In [51]:
init_params = collect.(eachrow(result_multi.draws_transformed.value[1:nchains, :, 1]));

Let us now start the NUTS chains.

In [18]:
chains_planck_nuts = sample(CMB_model_planck, NUTS(nadapts, 0.65), MCMCThreads(), nsteps, nchains; init_params)

┌ Info: Found initial step size
└   ϵ = 0.0007568359375
┌ Info: Found initial step size
└   ϵ = 0.00078125
┌ Info: Found initial step size
└   ϵ = 0.00078125
┌ Info: Found initial step size
└   ϵ = 0.00078125
┌ Info: Found initial step size
└   ϵ = 0.00078125
┌ Info: Found initial step size
└   ϵ = 0.00078125
Sampling (6 threads): 100%|█████████████████████████████| Time: 0:01:54


Chains MCMC chain (5000×19×6 Array{Float64, 3}):

Iterations        = 501:1:5500
Number of chains  = 6
Samples per chain = 5000
Wall duration     = 1587.05 seconds
Compute duration  = 9152.81 seconds
parameters        = ln10As, ns, h0, ωb, ωc, τ, yₚ
internals         = lp, n_steps, is_accept, acceptance_rate, log_density, hamiltonian_energy, hamiltonian_energy_error, max_hamiltonian_energy_error, tree_depth, numerical_error, step_size, nom_step_size

Summary Statistics
  parameters      mean       std   naive_se      mcse          ess      rhat   ⋯
      Symbol   Float64   Float64    Float64   Float64      Float64   Float64   ⋯

      ln10As    0.3051    0.0017     0.0000    0.0000   11492.7176    1.0006   ⋯
          ns    0.9630    0.0044     0.0000    0.0000   10687.6754    1.0008   ⋯
          h0    0.6705    0.0060     0.0000    0.0001    8844.1047    1.0013   ⋯
          ωb    0.2234    0.0015     0.0000    0.0000   12355.8873    1.0008   ⋯
          ωc    0.1207    0.0014     0.

Let us plot our chains. As we can see, the samples looks almost uncorrelated, which is consistent with our estimate of the correlation length, which is between 2-3 for cosmological parameters.

In [19]:
p = StatsPlots.plot(chains_planck_nuts)
StatsPlots.savefig("traceplots_Planck.png")
p

In [21]:
chain_planck = combine_chains(chains_planck_nuts)
npzwrite("chains_Planck_NUTS.npy", chain_planck)

An interesting quantity we will compare with the MCHMC run is the ESS per second

In [71]:
CPU_s_Planck_NUTS = compute_duration(chains_planck_nuts)
Planck_NUTS_ESS = mean(MCMCDiagnosticTools.ess_rhat(chains_planck_nuts)[[:ln10As, :ns, :h0, :ωb,:ωc, :τ, :yₚ],:ess])
Planck_NUTS_ESS_s = Planck_NUTS_ESS/CPU_s_Planck_NUTS

1.611871401941995

An ESS/s of 1.6 means that we can reach the (heuristic) threshold of 400 ESS in around 4 minutes and, taking advantage of the multiple processor, our analysis can be performed in around 1 minute.

## The MicroCanonical Hamiltonian MonteCarlo sampler
Here we will use the Julia implementation of the MCHMC sampler.
We will use 20'000 adaptation steps (that will be discarded) and 200'000 steps.

In [72]:
d = 7
target = TuringTarget(CMB_model_planck)
nadapts = 20_000
nsteps = 200_000
spl = MCHMC(nadapts, 0.001; init_eps=0.05, L=sqrt(d),# sigma=ones(d),
            adaptive=true)
@time planck_mchmc = Sample(spl, target, nsteps;
                       progress=true,
                       dialog=true, file_name="chain_1",
                       initial_x=bestfit_Planck.values.array)

[ Info: Tuning sigma ⏳
[ Info: Tuning eps ⏳
MCHMC (tuning):  20%|███████                            |  ETA: 0:00:37

Burn in step: 4000
eps --->0.0009149843121289433


MCHMC (tuning):  40%|██████████████                     |  ETA: 0:00:29

Burn in step: 8000
eps --->0.029262998262257686


MCHMC (tuning):  60%|█████████████████████              |  ETA: 0:00:20

...

2mMCHMC (tuning): 100%|███████████████████████████████████| Time: 0:00:50

Burn in step: 20000
eps --->0.03916564751790155


[ Info: eps: 0.03916564751790155
[ Info: L: 2.6457513110645907
[ Info: nu: 0.06551889030551221
[ Info: sigma: [0.1741002427813197, 0.2835893274207752, 0.9257817194835208, 0.5192878653001441, 0.16757764532072955, 0.020525365313651952, 0.0031432132271582537]
[ Info: adaptive: true
2mMCHMC: 100%|████████████████████████████████████████████| Time: 0:08:14

545.734258 seconds (2.01 G allocations: 777.675 GiB, 15.14% gc time)


200000-element Vector{Any}:
 [0.30456956845438293, 0.9666357297556083, 0.672257203906617, 0.2236452791093787, 0.12046547141005495, 0.054703996074012017, 1.0001285577409693, 0.03916564751790155, -0.10066052697698069, -854.0500821925881]
 [0.30455293928499266, 0.9665933981014776, 0.6719037324580928, 0.22386867412756206, 0.1203858543128654, 0.0546550914715772, 1.000123667737461, 0.03939033223849663, -0.005842627972469927, -853.9122261208879]
 [0.3045415685897251, 0.9665778400728448, 0.6717239247798523, 0.22410890203821524, 0.12031966357569766, 0.054734514222638406, 1.000127627563567, 0.0394891666078293, 0.06638601753763851, -854.337559662091]
 [0.30451470144639053, 0.9665007399296267, 0.6721171217781738, 0.22434490142946986, 0.1202743411461021, 0.05488073874404311, 1.000128857447913, 0.03973329609227235, -0.018608041080256044, -854.2913339168705]
 [0.3044852179337628, 0.9663677408230082, 0.6728775663115266, 0.22456155296853367, 0.12025891377059872, 0.05501813095907154, 1.0001268017077134,

In [30]:
n_parallel_mchmc = 8
chains = Vector{Any}(undef, n_parallel_mchmc)
vec_ess = zeros(n_parallel_mchmc)

nadapts = 20_000
nsteps = 200_000
start_mchmc = time()

@time for i in 1:n_parallel_mchmc
    chains[i] = Sample(MCHMC(nadapts, 0.001; init_eps=0.05, L=sqrt(d), adaptive=true), target, nsteps;
                       progress=true,
                       dialog=true, file_name="chain_1",
                       initial_x=bestfit_Planck.values.array)
    vec_ess[i] = mean(Summarize(chains[i])[1][1:7])
end

end_mchmc = time()
time_mchmc_parallel_Planck = end_mchmc - start_mchmc

[ Info: Tuning sigma ⏳
[ Info: Tuning eps ⏳
MCHMC (tuning):  20%|██████▉                            |  ETA: 0:00:37

Burn in step: 4000
eps --->0.0011990461342559944


MCHMC (tuning):  40%|██████████████                     |  ETA: 0:00:28

Burn in step: 8000
eps --->0.010212162332368293


MCHMC (tuning):  60%|█████████████████████              |  ETA: 0:00:19

...

2mMCHMC (tuning): 100%|███████████████████████████████████| Time: 0:00:47

Burn in step: 20000
eps --->0.026265107159019377


[ Info: eps: 0.026265107159019377
[ Info: L: 2.6457513110645907
[ Info: nu: 0.05352298224705687
[ Info: sigma: [0.12694210472403483, 0.7044908096097218, 0.4823595698107095, 0.616718456787119, 0.547009401312155, 0.00896888255363675, 0.0025460528034231367]
[ Info: adaptive: true
2mMCHMC: 100%|████████████████████████████████████████████| Time: 0:07:47

4139.929642 seconds (16.10 G allocations: 6.122 TiB, 13.47% gc time)


4139.9618990421295

Let us compute the ESS per second of the parallel MCHMC run.

In [31]:
Planck_MCHMC_parallel_ESS_s = sum(vec_ess)/time_mchmc_parallel_Planck

5.0327120016453835

This is higher by a factor of 3 than the NUTS ESS/s!

In [32]:
_chains = zeros(nsteps, n_parallel_mchmc, 7)
for i in 1:n_parallel_mchmc
    _chains[:,i,:] = mapreduce(permutedims, vcat, chains[i])[:,1:7]
end

In [73]:
planck_mchmc = mapreduce(permutedims, vcat, planck_mchmc)
E = planck_mchmc[:, end-1]
std(E).^2/d

0.0010243159775626906

In [34]:
x = [mapreduce(permutedims, vcat, chains[i]) for i in 1:n_parallel_mchmc]

planck_mchmc_multi_chains = zeros(nsteps*n_parallel_mchmc, 7)
for i in 1:7
    planck_mchmc_multi_chains[:,i] = extract_single(x, i, n_parallel_mchmc)
end

In [74]:
npzwrite("chains_Planck_MCHMC.npy", planck_mchmc)
npzwrite("chains_Planck_MCHMC_multi.npy", planck_mchmc_multi_chains)